# Import the relevant libraries

In [8]:
import pandas as pd
from creapy import creapy
import plotly
from pathlib import Path
import sys
import logging
import os
import time
import librosa
import numpy as np
import torch
from scipy.io.wavfile import write
from tqdm import tqdm
import utils
from models import SynthesizerTrn
from speaker_encoder.voice_encoder import SpeakerEncoder
from wavlm import WavLM, WavLMConfig
from datetime import datetime
import IPython.display as ipd 
import json
from praatio import textgrid as tg
from praatio.utilities.constants import Interval

## Load the models and helper functions
This includes setting location of the downloaded checkpoint off WavLM and the FreeVC model to be used

In [9]:
wavlm_large_path = 'wavlm/WavLM-Large.pt'
freevc_chpt_path = 'logs/freevc_cpps/G_182000.pth'
#creapy.set_config(creak_threshold=0.5)

def arg_creator(source, target, outpath, creak_values, cpps_values):
    return [source, target, outpath, creak_values, cpps_values]

def get_cmodel():
    checkpoint = torch.load(wavlm_large_path)
    cfg = WavLMConfig(checkpoint['cfg'])
    cmodel = WavLM(cfg)
    cmodel.load_state_dict(checkpoint['model'])
    cmodel.eval()

    return cmodel

def generate_timestamp():
    # Get the current date and time
    now = datetime.now()

    # Format the date and time as a string suitable for a filename
    #timestamp = now.strftime("%Y%m%d_%H%M%S")
    timestamp = now.strftime("%Y%m%d_%H%M%S_") + str(int(now.microsecond / 1000)).zfill(2)
    # Return the formatted timestamp with the desired file extension
    return timestamp

def convert(args):
    print("converting...")
    wav_tgt1, _ = librosa.load(args[1], sr=hps.data.sampling_rate)
    wav_tgt1, _ = librosa.effects.trim(wav_tgt1, top_db=20)
    g_tgt1 = smodel.embed_utterance(wav_tgt1)
    g_tgt = torch.from_numpy(g_tgt1).unsqueeze(0)

    # src
    wav_src, _ = librosa.load(args[0], sr=hps.data.sampling_rate)
    wav_src = torch.from_numpy(wav_src).unsqueeze(0)

    c = utils.get_content(cmodel, wav_src)
    try:
        tgt_audio = net_g.infer(c, g=g_tgt, creaks=torch.tensor(np.zeros((1, 1, (wav_src.size(1)//320-1))), dtype=torch.float32)+args[3], cpps=torch.tensor(np.zeros((1, 1, (wav_src.size(1)//320-1))), dtype=torch.float32)+args[4])
    except:
        tgt_audio = net_g.infer(c, g=g_tgt, creaks=torch.tensor(np.zeros((1, 1, (wav_src.size(1)//320))), dtype=torch.float32)+args[3], cpps=torch.tensor(np.zeros((1, 1, (wav_src.size(1)//320))), dtype=torch.float32)+args[4])
    tgt_audio = tgt_audio[0][0].data.cpu().float().numpy()

    timestamp = generate_timestamp()
    print(timestamp)
    ipd.display(ipd.Audio(tgt_audio, rate=hps.data.sampling_rate))
    write(args[2], hps.data.sampling_rate, tgt_audio)
    #calculate cosine distance between speaker embedding of target and converted audio
    final_embedding = smodel.embed_utterance(tgt_audio)
    #torch cosine distance
    print(g_tgt1.shape, final_embedding.shape)
    cosine_distance = torch.nn.functional.cosine_similarity(torch.from_numpy(g_tgt1).unsqueeze(0), torch.from_numpy(final_embedding).unsqueeze(0))
    print(cosine_distance)
 
    return tgt_audio

def create_creak_tensor(wav_len, creak_segments, sr):
    #create tensor torch.tensor(np.zeros((1, 1, (wav_src.size(1)//320-1))), dtype=torch.float32)) and then add the creak value to the tensor between the start and end frames
    #creak_start and creak_end are in seconds
    #start and end are in seconds

    #convert start and end to frames
    end_frame = (wav_len // 320)
    creak_frames = [(int(item[0] * sr // 320), int(item[1] * sr // 320), item[2]) for item in creak_segments]
    creaks = torch.tensor(np.zeros((1, 1, (end_frame))), dtype=torch.float32)

    for creak in creak_frames:
        creaks[0, 0, creak[0]:creak[1]] = creak[2]
    return creaks

def json_to_textgrid(json_path, textgrid_path):
    with open(json_path) as f:
        data = json.load(f)
    start_speech = data['segments'][0]['start']
    end_speech = data['segments'][0]['end']
    timestamps = data['segments'][0]['words']

    textgrid = tg.Textgrid()
    tier = tg.IntervalTier('word', [], start_speech, end_speech)

    new_timestamps = []
    for i, timestamp in enumerate(timestamps):
        prev_timestamp = timestamps[i-1] if i > 0 else None
        if prev_timestamp:
            if prev_timestamp['end'] == timestamp['start']:
                start = prev_timestamp['end']
            else:
                start = prev_timestamp['end'] + 0.01
            end = timestamp['end']
            new_timestamps.append({'start': start, 'end': end, 'word': timestamp['word']})
            tier.insertEntry(Interval(start, end, timestamp['word']))
        else:
            tier.insertEntry(Interval(timestamp['start'], timestamp['end'], timestamp['word']))
            new_timestamps.append({'start': timestamp['start'], 'end': timestamp['end'], 'word': timestamp['word']})
    textgrid.addTier(tier)
    textgrid.save(textgrid_path, format='long_textgrid', includeBlankSpaces=False)
    return new_timestamps

hps = utils.get_hparams_from_file('configs/freevc.json')

net_g = SynthesizerTrn(
    hps.data.filter_length // 2 + 1,
    hps.train.segment_size // hps.data.hop_length,
    **hps.model
)

utils.load_checkpoint(freevc_chpt_path, net_g, optimizer=None, strict=True)
cmodel = get_cmodel()
smodel = SpeakerEncoder('speaker_encoder/ckpt/pretrained_bak_5805000.pt', device='cpu')

/home/lameris/miniconda3/envs/CreakVC/lib/python3.8/site-packages/torch/nn/utils/weight_norm.py:28: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


INFO:root:Loaded checkpoint 'logs/freevc_cpps/G_182000.pth' (iteration 1916)
INFO:wavlm.WavLM:WavLM Config: {'extractor_mode': 'layer_norm', 'encoder_layers': 24, 'encoder_embed_dim': 1024, 'encoder_ffn_embed_dim': 4096, 'encoder_attention_heads': 16, 'activation_fn': 'gelu', 'layer_norm_first': True, 'conv_feature_layers': '[(512,10,5)] + [(512,3,2)] * 4 + [(512,2,2)] * 2', 'conv_bias': False, 'feature_grad_mult': 1.0, 'normalize': True, 'dropout': 0.0, 'attention_dropout': 0.0, 'activation_dropout': 0.0, 'encoder_layerdrop': 0.0, 'dropout_input': 0.0, 'dropout_features': 0.0, 'mask_length': 10, 'mask_prob': 0.8, 'mask_selection': 'static', 'mask_other': 0.0, 'no_mask_overlap': False, 'mask_min_space': 1, 'mask_channel_length': 10, 'mask_channel_prob': 0.0, 'mask_channel_selection': 'static', 'mask_channel_other': 0.0, 'no_mask_channel_overlap': False, 'mask_channel_min_space': 1, 'conv_pos': 128, 'conv_pos_groups': 16, 'relative_position_embedding': True, 'num_buckets': 320, 'max_dis

## Set the arguments
Here we set the following arguments for the creaky voice conversion:

1. **source_path** indicates the audio file of which we want the linguistic content.
2. **target_path** indicates the audio file containing speech of the target speaker.
3. **outpath** is the location where the converted audio will be saved.
4. **average_creak** is the initial creak value over the complete utterance that will be supplied to the model 

We also create the output folder specified in the arguments


In [16]:
source_path = "test_audio/16000_joe_example.wav"
target_path = "test_audio/16000_male_voice.wav"
outpath = "data/out/creaky_vctk_liam_cpp.wav"
average_creak = 2
average_cpps = 1

args = arg_creator(source_path, target_path, outpath, average_creak, average_cpps)
os.makedirs('/'.join(args[2].split('/')[:-1]), exist_ok=True)

In [17]:
ipd.display(ipd.Audio(args[0], rate=16000))
ipd.display(ipd.Audio(args[1], rate=16000))

# Perform the conversion

In [18]:
creaky_audio = convert(args)

converting...
20240916_134022_87


(256,) (256,)
tensor([0.8817])


## Run WhisperX
* We run speech recognition to transcribe the generated utterance
* We convert the timestamps from json to TextGrid in order to use prepare them for CreaPy 

In [13]:
#run whisper
!whisperx "data/out/creaky_vctk_liam_cpp.wav" --model medium.en --output_dir data/out/creaky_vctk_whisper --language en --verbose=False

#read json file with the start and end times of the words
timestamps = json_to_textgrid('data/out/creaky_vctk_whisper/creaky_vctk_liam_cpp.json', 'data/out/creaky_vctk_whisper/creaky_vctk_liam_cpp.TextGrid')
print(timestamps)

/home/lameris/miniconda3/envs/CreakVC/lib/python3.8/site-packages/pyannote/audio/core/io.py:43: UserWarning: torchaudio._backend.set_audio_backend has been deprecated. With dispatcher enabled, this function is no-op. You can remove the function call.
  torchaudio.set_audio_backend("soundfile")
Lightning automatically upgraded your loaded checkpoint from v1.5.4 to v2.2.4. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint ../.cache/torch/whisperx-vad-segmentation.bin`
Model was trained with pyannote.audio 0.0.1, yours is 3.1.1. Bad things might happen unless you revert pyannote.audio to 0.x.
Model was trained with torch 1.10.0+cu102, yours is 2.3.0+cu121. Bad things might happen unless you revert torch to 1.x.
>>Performing transcription...
>>Performing alignment...
[{'start': 0.249, 'end': 0.71, 'word': 'where'}, {'start': 0.72, 'end': 1.291, 'word': 'they'}, {'start': 1.301, 'end': 1.492, 'word': 'just'}, {'start': 1.502, 'end'

## Run CreapPy
This enables us to quantify and visualize the creak probability

In [14]:
X_test, y_pred, sr = creapy.process_file(textgrid_path='./data/out/creaky_vctk_whisper/creaky_vctk_liam_cpp.TextGrid', audio_path='./data/out/creaky_vctk_liam_cpp.wav')

/home/lameris/CreakVC/creapy/creapy/feature_extraction/feature_extraction.py:74: RuntimeWarning:

Mean of empty slice.

/home/lameris/miniconda3/envs/CreakVC/lib/python3.8/site-packages/numpy/core/_methods.py:189: RuntimeWarning:

invalid value encountered in double_scalars



Wrote textgrid at /home/lameris/CreakVC/data/out/creaky_vctk_whisper/creaky_vctk_liam_cpp.TextGrid


## Smoothen the output

In [15]:
y_pred_smoothed = np.convolve(y_pred, np.ones(10)/10, mode='same')

## Plot the creak

In [9]:
fig = creapy.plot(X_test, y_pred_smoothed, sr, words=timestamps)

In [15]:
#new_creaks = create_creak_tensor(creaky_audio.shape[0], [(0.589, 0.81, -4), (0.81, 1.04, -10), (1.19, 1.49, -14), (1.87, 2.0, -10), (2.0, 2.98, 5)], sr)
new_creaks = create_creak_tensor(creaky_audio.shape[0], [(0.01, 6.7, 40)], sr)
args[-1] = new_creaks

new_creaky_audio = convert(args)

converting...
20240610_093347_558


In [21]:
#run creapy on output audio
X_test, y_pred, sr, = creapy.process_file(textgrid_path='./data/out/creaky_vctk_whisper/creaky_vctk_liam.TextGrid', audio_path='./data/out/creaky_vctk_liam.wav')
y_pred_smoothed = np.convolve(y_pred, np.ones(10)/10, mode='same')
fig2 = creapy.plot(X_test, y_pred_smoothed, sr, words=timestamps)

/home/lameris/CreakVC/creapy/creapy/feature_extraction/feature_extraction.py:74: RuntimeWarning:

Mean of empty slice.

/home/lameris/miniconda3/envs/CreakVC/lib/python3.8/site-packages/numpy/core/_methods.py:189: RuntimeWarning:

invalid value encountered in double_scalars



Wrote textgrid at /home/lameris/CreakVC/data/out/creaky_vctk_whisper/creaky_vctk_liam.TextGrid


In [13]:
#run creapy on output audio
X_test, y_pred, sr, = creapy.process_file(textgrid_path='./data/out/creaky_vctk_whisper/creaky_vctk_liam.TextGrid', audio_path='./data/out/creaky_vctk_liam.wav')
y_pred_smoothed = np.convolve(y_pred, np.ones(10)/10, mode='same')
fig2 = creapy.plot(X_test, y_pred_smoothed, sr, words=timestamps)


/home/lameris/CreakVC/creapy/creapy/feature_extraction/feature_extraction.py:74: RuntimeWarning:

Mean of empty slice.

/home/lameris/miniconda3/envs/CreakVC/lib/python3.8/site-packages/numpy/core/_methods.py:189: RuntimeWarning:

invalid value encountered in double_scalars



Wrote textgrid at /home/lameris/CreakVC/data/out/creaky_vctk_whisper/creaky_vctk_liam.TextGrid
